In [5]:
import os,re,time,json

"""
模板文件目录下 题目清单.tex 文件不能缺失
"""

"""---设置题目列表---"""
#字典字段为文件名, 之后为内容的题号
problems_dict = {
"K0501001B" : "3327,139,1851,1848",
"K0501003B" : "3352,138,139,515,1847,1854",
"K0501004B" : "3346,1871,1915,3327,139,140,1846,1851,1856,1857",
"K0501005B" : "1857",
"K0501006B" : "3327,1847,1851",
"K0502001B" : "919",
"K0502002B" : "3326,3331,3332",
"K0502004B" : "1850,1852,1856",
"K0502006B" : "1852",
"K0502007B" : "3326,3343,515,1856",
"K0503001B" : "3328,3346,140,883,1856",
"K0503002B" : "3343,3347,1888,1889,1857",
"K0503003B" : "3329,1858",
"K0503005B" : "1869,1873",
"K0506001B" : "1861",
"K0506003B" : "1870,1868,3355,3361,1867,1904,1910,3333,3337,145,535,785,930,1860,1866",
"K0507007B" : "3343,1888,1889,143,144,146,155,156",
"K0507009B" : "143,144",
"K0509001B" : "3351,1894,1907,143,150,155,1865,1874",
"K0509002B" : "3344,3353,3358,1895,148,151,1859,1864",
"K0509003B" : "3348,3336,1862,1863,1872",
"K0504002B" : "481,894",
"K0504003B" : "3347,1912,3334",
"K0504006B" : "3339,3352,1878,1897,1914,1917,3328,3330,973,947,153,154,871,1877",
"K0504007B" : "3356,1901,1878,947,414,481,760,894",
"K0505001B" : "1882,1883,792,819,1849",
"K0505003B" : "1885,141,142,919,936,1853,1880",
"K0505004B" : "3338,1900,154,1879",
"K0505005B" : "3340,3341,3342,3349,3354,1884,1897,1900,1906,3330,3334,139,142,152,699,792,919,936,1849,1853",
"K0508003B" : "3349,3335,1890,1892,1893,1896,1899,1908,1913,855,141,144,152,156,554,699",
"K0508004B" : "3340,3347,3360,1916,1886,1889,1891,1898,1903,152,147,157,819",
"K0508005B" : "3345,3350,3357,3360,1916,1887,1898,149",
"K0509004B" : "3358,3359,1881,1905,1909,1911,1875,147,158,160,161,955,1876",
"K0510001B" : "1902",
"K0510003B" : "159"


}

"""---设置题目列表结束---"""

"""---设置文件保存路径---"""
#目录和文件的分隔务必用/
directory = "临时文件/批量生成题目/"
"""---设置文件名结束---"""



#生成数码列表, 逗号分隔每个区块, 区块内部用:表示整数闭区间
def generate_number_set(string,dict):
    string = re.sub(r"[\n\s]","",string)
    string_list = string.split(",")
    numbers_list = []
    for s in string_list:
        if not ":" in s:
            numbers_list.append(s.zfill(6))
        else:
            start,end = s.split(":")
            for ind in range(int(start),int(end)+1):
                numbers_list.append(str(ind).zfill(6))
    return numbers_list

#将正确率转化为含颜色代码的字符串
def get_color(value):
    value = float(value)
    if value>=0.5:
        (r,g,b)=(1,2-2*value,0)
    else:
        (r,g,b)=(2*value,1,0)
    return "{" + "%.3f" %(r) + "," + "%.3f" %(g) + ",0}"


def color_value(matchobj):
    value = matchobj.group(1)
    return "\t"+"\\fcolorbox[rgb]{0,0,0}"+ get_color(value) +"{" + value +"}"


#读取题库json文件并转化为字典
with open(r"../题库0.3/Problems.json","r",encoding = "utf8") as f:
    database = f.read()
pro_dict = json.loads(database)

#读取目标数据库json并转化为字典
with open(r"../题库0.3/LessonObj.json","r",encoding = "utf8") as f:
    database = f.read()
obj_dict = json.loads(database)

try:
    os.mkdir(directory)
except:
    pass

#读取系统日期
current_time = time.localtime()
time_string = "_"+str(current_time.tm_year).zfill(4)+str(current_time.tm_mon).zfill(2)+str(current_time.tm_mday).zfill(2)

for filename in problems_dict:
    problems = problems_dict[filename]
    teachers_latex_file = directory + filename + "_教师用" + time_string + ".tex"
    students_latex_file = directory + filename + "_学生用" + time_string + ".tex"

    #生成题目列表
    problem_list = [id for id in generate_number_set(problems.strip(),pro_dict) if id in pro_dict]

    data_teachers = ""
    data_students = ""
    id_list = ""

    #生成教师题目字符串与学生题目字符串, 准备替换至latex文件
    for id in problem_list:
        problemset = pro_dict[id]
        problem = problemset["content"]
        solution = (problemset["solution"] if problemset["solution"] != "" else "暂无解答与提示")
        answer = (problemset["ans"] if problemset["ans"] != "" else "暂无答案")
        usages_list = problemset["usages"]
        if len(usages_list) > 0:
            usage = re.sub("\\t([\d]\.[\d]{0,10})",color_value,"\n\n".join(usages_list))
            usage = re.sub("[\\t ]([\d]\.[\d]{0,10})",color_value,usage)
        else:
            usage = "暂无使用记录"
        origin = (problemset["origin"] if problemset["origin"] != "" else "出处不详")
        objects = problemset["objs"]
        if len(objects) == 0:
            objects = "暂未关联目标\n\n"
        elif "KNONE" in [o.upper() for o in objects]:
            objects = "该题的考查目标不在目前的集合中\n\n"
        else:
            objects_string = ""
            for obj in objects:
                if not obj in obj_dict:
                    objects_string = "目标" + obj + "有误\n\n"
                    break
                else:
                    objects_string += obj + "|" + obj_dict[obj]["content"] + "\n\n"
            objects = objects_string
        space = ("" if problemset["space"] == "" else r"\vspace*{"+problemset["space"]+"}\n")
        tags = ("|".join(problemset["tags"]) if len(problemset["origin"])>0 else "暂无标签")
        raw_string = "\\item " + "{\\tiny ("+id+")}"+problem
        teachers_string = raw_string.replace("\\tiny","")+"\n\n关联目标:\n\n"+ objects + "\n\n标签: " + tags + "\n\n答案: "+answer + "\n\n" + "解答或提示: " + solution + "\n\n使用记录:\n\n"+ usage + "\n" + "\n\n出处: "+origin + "\n"
        students_string = raw_string + space + "\n\n"
        data_teachers += teachers_string
        data_students += students_string



    #替换latex文件的内容并编译
    with open("模板文件/题目清单.tex","r",encoding = "utf8") as f:
        latex_raw = f.read()
    latex_teachers = latex_raw.replace("编译模板",data_teachers)
    with open(teachers_latex_file,"w",encoding = "utf8") as f:
        f.write(latex_teachers)
    print("开始编译教师版本pdf文件: ", teachers_latex_file)
    os.system("xelatex -interaction=batchmode -output-directory=" + directory + " "+ teachers_latex_file)
    print(os.system("xelatex -interaction=batchmode -output-directory=" + directory + " "+ teachers_latex_file))

    latex_students = latex_raw.replace("编译模板",data_students)
    with open(students_latex_file,"w",encoding = "utf8") as f:
        f.write(latex_students)
    print("开始编译学生版本pdf文件: ", students_latex_file)
    os.system("xelatex -interaction=batchmode -output-directory=" + directory + " "+ students_latex_file)
    print(os.system("xelatex -interaction=batchmode -output-directory=" + directory + " "+ students_latex_file))


开始编译教师版本pdf文件:  临时文件/批量生成题目/K0501001B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0501001B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0501003B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0501003B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0501004B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0501004B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0501005B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0501005B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0501006B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0501006B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0502001B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0502001B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0502002B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0502002B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0502004B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K0502004B_学生用_20220922.tex
0
开始编译教师版本pdf文件:  临时文件/批量生成题目/K0502006B_教师用_20220922.tex
0
开始编译学生版本pdf文件:  临时文件/批量生成题目/K05

In [2]:
problems

['3327', '139', '1851', '1848']